This tutorial walks through the process of using Snowflake Data Clean Rooms with Snowpark Container Services (SPCS). This is the consumer notebook in this tutorial. You should also upload the provider notebook in another account with the clean rooms API installed.

**Prerequisites for synthetic data generation**

- `scikit-learn` needs to be added in the Python packages drop down. This is needed for the synthetic data generation code.
- 4XL Snowpark-optimized warehouse is needed for larger data sizes, for example: 100M. And it takes some time.

Ensure your account has the latest Data Clean Rooms version.

In [ ]:
USE ROLE samooha_app_role;
CALL samooha_by_snowflake_local_db.library.apply_patch();

Use the code below to generate synthetic consumer dataset. Use a 4XL warehouse.

In [ ]:
USE ROLE ACCOUNTADMIN;
CREATE DATABASE IF NOT EXISTS SAMOOHA_SAMPLE_LOOKALIKE_DATABASE;

In [ ]:
import pandas as pd
import numpy as np
from sklearn.datasets import make_classification
from snowflake.snowpark.context import get_active_session

DATABASE_NAME = "SAMOOHA_SAMPLE_LOOKALIKE_DATABASE"
SCHEMA_NAME = "PUBLIC"
TABLE_NAME = "SEED_CUSTOMERS"

PROVIDER_SIZE = 100000000
CONSUMER_SIZE = int(PROVIDER_SIZE * 0.35)

def generate_dcr_datasets(n_features: int = 20, provider_size_count: int = PROVIDER_SIZE, consumer_size_count: int = CONSUMER_SIZE):
    X, Y = make_classification(flip_y=0.13, n_samples=provider_size_count, n_features=n_features, n_redundant=0, random_state=1,
                               **{"n_informative": 1, "n_clusters_per_class": 1, "n_classes": 2})
    provider_df = pd.concat([pd.DataFrame(X), pd.DataFrame(Y)], axis=1)
    
    column_name_list = ['FEATURE_' + str(i) for i in range(n_features)] + ['TARGET']
    provider_df.columns = column_name_list
    provider_df['EMAIL'] = provider_df.reset_index()['index'].apply(lambda x:f"email_{x}@fakecorp.com")
    
    random_indices = np.random.choice(provider_df.index, size=consumer_size_count, replace=False)
    consumer_df = provider_df.loc[random_indices].reset_index()[['EMAIL','TARGET']]
    provider_df.drop(columns=['TARGET'], inplace=True)
    return provider_df, consumer_df

_, consumer_df = generate_dcr_datasets()
session = get_active_session()
session.write_pandas(consumer_df, TABLE_NAME, database=DATABASE_NAME, schema=SCHEMA_NAME, auto_create_table=True, overwrite=True)
print(f"Generated synthetic consumer data: {DATABASE_NAME}.{SCHEMA_NAME}.{TABLE_NAME}")

In [ ]:
USE ROLE ACCOUNTADMIN;
CALL samooha_by_snowflake_local_db.consumer.register_db('SAMOOHA_SAMPLE_LOOKALIKE_DATABASE');

USE ROLE SAMOOHA_APP_ROLE;
SELECT COUNT(*) FROM SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.SEED_CUSTOMERS;

Install the clean room shared by the provider and link the consumer datasets.

In [ ]:
USE ROLE samooha_app_role;
SET cleanroom_name = 'SPCS Lookalike Demo';

CALL samooha_by_snowflake_local_db.consumer.install_cleanroom(
    $cleanroom_name,
    '<PROVIDER_ACCOUNT_LOCATOR>'
);

CALL samooha_by_snowflake_local_db.consumer.link_datasets(
    $cleanroom_name,
    [ 'SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.SEED_CUSTOMERS' ]
);

Create a compute pool and grant the clean room access to the compute pool as well as a warehouse, if the service runs queries.

In [ ]:
USE ROLE ACCOUNTADMIN;
-- Grant access to a warehouse to run queries
GRANT USAGE ON WAREHOUSE APP_WH TO APPLICATION SAMOOHA_CLEANROOM_APP_SPCS_Lookalike_Demo;

-- Grant SAMOOHA_APP_ROLE privileges to create compute pools and create services
GRANT CREATE COMPUTE POOL ON ACCOUNT TO ROLE SAMOOHA_APP_ROLE WITH GRANT OPTION;
GRANT BIND SERVICE ENDPOINT ON ACCOUNT TO ROLE SAMOOHA_APP_ROLE WITH GRANT OPTION;

-- Create the compute pool
USE ROLE SAMOOHA_APP_ROLE;
CREATE COMPUTE POOL DCR_LAL_POOL
    FOR APPLICATION SAMOOHA_CLEANROOM_APP_SPCS_Lookalike_Demo
    min_nodes = 1 max_nodes = 1
    instance_family = highmem_x64_l
    auto_resume = true;

-- Grant access to the compute pool
GRANT USAGE ON COMPUTE POOL DCR_LAL_POOL TO APPLICATION SAMOOHA_CLEANROOM_APP_SPCS_Lookalike_Demo;
-- Allow to create the service
GRANT BIND SERVICE ENDPOINT ON ACCOUNT TO APPLICATION SAMOOHA_CLEANROOM_APP_SPCS_Lookalike_Demo;

Once the grants are set up, start the service.

If the provider allowed monitoring of the service, [service container logs can be retrieved](https://docs.snowflake.com/en/sql-reference/functions/system_get_service_logs).

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.start_or_update_service(
    $cleanroom_name,
    'dcr_lal_pool',
    object_construct(
        'query_warehouse', 'app_wh',
        'min_instances', '1',
        'max_instances', '1'
));

-- See endpoints in the service, including URL for public endpoints.
SHOW ENDPOINTS IN SERVICE SAMOOHA_CLEANROOM_APP_SPCS_Lookalike_Demo.services.service;

-- See the state of the service.
DESC SERVICE SAMOOHA_CLEANROOM_APP_SPCS_Lookalike_Demo.services.service;

In [ ]:
-- If the provider allowed monitoring, service logs can be retrieved.
SELECT VALUE AS log_line
  FROM TABLE(
    SPLIT_TO_TABLE(system$get_service_logs(
        'SAMOOHA_CLEANROOM_APP_SPCS_Lookalike_Demo.services.service', 0, 'lal'), '\n')
  );

It takes a few minutes for the service to start (in state RUNNING). Once it is running, you can run the analysis.

In [ ]:
-- Run training via lal_train template.
-- Model is kept in the service memory.
CALL samooha_by_snowflake_local_db.consumer.run_analysis(
    $cleanroom_name,
    'lal_train',
    ['SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.SEED_CUSTOMERS'],
    ['SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS'],
    OBJECT_CONSTRUCT(
        'provider_join_col', 'p.EMAIL',
        'consumer_join_col', 'c.EMAIL',
        'dimensions', ['p.FEATURE_0', 'p.FEATURE_1', 'p.FEATURE_2', 'p.FEATURE_3', 'p.FEATURE_4', 'p.FEATURE_5', 'p.FEATURE_6', 'p.FEATURE_7', 'p.FEATURE_8', 'p.FEATURE_9', 'p.FEATURE_10', 'p.FEATURE_11', 'p.FEATURE_12', 'p.FEATURE_13', 'p.FEATURE_14', 'p.FEATURE_15', 'p.FEATURE_16', 'p.FEATURE_17', 'p.FEATURE_18', 'p.FEATURE_19'],
        'filter_clause', 'c.TARGET = 1'
    )
);

In [ ]:
-- Run inference via lal_score template.
-- Training needs to be performed first to make the model available.
CALL samooha_by_snowflake_local_db.consumer.run_analysis(
    $cleanroom_name,
    'lal_score',
    ['SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.SEED_CUSTOMERS'],
    ['SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS'],
    OBJECT_CONSTRUCT(
        'provider_join_col', 'p.EMAIL',
        'consumer_join_col', 'c.EMAIL',
        'dimensions', ['p.FEATURE_0', 'p.FEATURE_1', 'p.FEATURE_2', 'p.FEATURE_3', 'p.FEATURE_4', 'p.FEATURE_5', 'p.FEATURE_6', 'p.FEATURE_7', 'p.FEATURE_8', 'p.FEATURE_9', 'p.FEATURE_10', 'p.FEATURE_11', 'p.FEATURE_12', 'p.FEATURE_13', 'p.FEATURE_14', 'p.FEATURE_15', 'p.FEATURE_16', 'p.FEATURE_17', 'p.FEATURE_18', 'p.FEATURE_19']
    )
);

In [ ]:
-- Run inference using lal_score_batches template.
-- Training needs to be performed first to make the model available.
-- Performance can be dramatically improved by establishing a multi-instance service.
CALL samooha_by_snowflake_local_db.consumer.run_analysis(
    $cleanroom_name,
    'lal_score_batches',
    ['SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.SEED_CUSTOMERS'],
    ['SAMOOHA_SAMPLE_LOOKALIKE_DATABASE.PUBLIC.CUSTOMERS'],
    OBJECT_CONSTRUCT(
        'provider_join_col', 'p.EMAIL',
        'consumer_join_col', 'c.EMAIL',
        'dimensions', ['p.FEATURE_0', 'p.FEATURE_1', 'p.FEATURE_2', 'p.FEATURE_3', 'p.FEATURE_4', 'p.FEATURE_5', 'p.FEATURE_6', 'p.FEATURE_7', 'p.FEATURE_8', 'p.FEATURE_9', 'p.FEATURE_10', 'p.FEATURE_11', 'p.FEATURE_12', 'p.FEATURE_13', 'p.FEATURE_14', 'p.FEATURE_15', 'p.FEATURE_16', 'p.FEATURE_17', 'p.FEATURE_18', 'p.FEATURE_19']
    )
);

If the provider updates the service, the consumer needs to receive the new patch of the clean room app first, then call `consumer.start_or_update_service` to apply the change.

Additionally, `consumer.start_or_update_service` can be used to change consumer-side configuration of the service, for example, the warehouse or the number of instances.

In [ ]:
USE ROLE SAMOOHA_APP_ROLE;
SET cleanroom_name = 'SPCS Lookalike Demo';

-- Ensure the provider's patch has been delivered.
DESCRIBE APPLICATION SAMOOHA_CLEANROOM_APP_SPCS_Lookalike_Demo;

In [ ]:
-- Update the service inside the clean room
CALL samooha_by_snowflake_local_db.consumer.start_or_update_service(
    $cleanroom_name,
    'dcr_lal_pool',
    OBJECT_CONSTRUCT(
        'query_warehouse', 'app_wh',
        'min_instances', '1',
        'max_instances', '1'
));

-- See the state of the service.
DESC SERVICE SAMOOHA_CLEANROOM_APP_SPCS_Lookalike_Demo.services.service;